In [1]:
import numpy as np
import pandas as pd
import pickle
import os
import matplotlib.pyplot as plt

import pandas_profiling
from scipy.stats import gmean

In [2]:
from sklearn.linear_model import LinearRegression, Ridge, Lasso, ElasticNet
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_squared_error

In [117]:
%matplotlib inline
random_seed = 42

pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)

In [22]:
def import_data(filepath):
    '''Converts space-separated values file into DataFrame.
    
    Arguments:
    filepath -- str, local file location
    
    Returns:
    df -- pd.DataFrame, labelled DataFrame
    '''
    
    col_names = ['engine_id', 'cycle', 'setting1', 'setting2', 'setting3']
    col_names.extend(['sensor%d' % i for i in range(1, 22)])
    col_names.append('dummy')  # Accounts for the trailing separator in the source data
    
    df = pd.read_csv(filepath, sep=' ', index_col=False, names=col_names)
    df.drop(labels='dummy', axis=1, inplace=True)  # Now drop that extra column

    return df

In [162]:
def add_target_cols(df, w0=30, w1=15):
    '''Adds regression and classification target columns to df.
    RUL -- Remaining Useful Life, the number of cycles until engine failure
    RUL_frac -- RUL fraction, the proportion of the engine's total lifetime remaining
    w0 -- cycles of RUL remaining at first warning
    w1 -- cycles of RUL remaining at last warning
    
    Arguments:
    df -- pd.DataFrame, fresh from import_data
    w0 -- int, (default 30)
    w1 -- int, (default 15)
    
    Returns:
    df -- pd.DataFrame, original df plus target columns
    '''
    
    df['max_cycles'] = df.groupby('engine_id')['cycle'].transform(max)  # Temporary column for memoization
    
    df['RUL'] = pd.Series(df['RUL'] + df['max_cycles'] - df['cycle'], dtype=int)
    df['max_RUL'] = df.groupby('engine_id')['RUL'].transform(max)  # Temporary column for memoization
    
    df['RUL_frac'] = df['RUL'] / df['max_RUL']
    
    df['w0'] = pd.Series(df['RUL'] <= w0, dtype=int)
    df['w1'] = df['w0'] + pd.Series(df['RUL'] <= w1, dtype=int)
    
    df.drop(labels=['max_cycles', 'max_RUL'], axis=1, inplace=True)  # Now drop those temp columns
    
    return df

In [163]:
def preprocess_train(filepath='./data/PM_train.txt'):
    train = import_data(filepath)
    train['RUL'] = 0
    train = add_target_cols(train)
    
    return train


def preprocess_val_test(filepath='./data/PM_test.txt'):
    np.random.seed(random_seed)
    val_test = import_data(filepath)

    RULs = pd.read_csv('./data/PM_truth.txt', names=['RUL'])
    RULs['engine_id'] = pd.Series([i for i in range(1, 101)])

    val_test = val_test.merge(RULs, on='engine_id')
    val_test = add_target_cols(val_test)
    
    val_ids = np.random.choice([i for i in range(1, 101)], size=50, replace=False, )

    val = val_test[val_test['engine_id'].isin(val_ids)].reset_index(drop=True)
    test = val_test[~val_test['engine_id'].isin(val_ids)].reset_index(drop=True)
    
    return val, test

In [164]:
def check_df_shapes(dfs):
    assert len(set([df.shape[1] for df in dfs])) == 1
    print('All dfs have the same number of columns')

In [165]:
train = preprocess_train()
val, test = preprocess_val_test()

check_df_shapes([train, val, test])

All dfs have the same number of columns


In [166]:
train.iloc[185:195]

engine_id  cycle  setting1  setting2  setting3  sensor1  sensor2  sensor3  sensor4  sensor5  sensor6  sensor7  sensor8  sensor9  sensor10  sensor11  sensor12  sensor13  sensor14  sensor15  sensor16  sensor17  sensor18  sensor19  sensor20  sensor21  RUL  RUL_frac  w0  w1
185          1    186    0.0027   -0.0003     100.0   518.67   643.51  1595.16  1426.30    14.62    21.61   552.57  2388.21  9051.37       1.3     48.12    520.08   2388.25   8123.45    8.5227      0.03       397      2388     100.0     38.47   23.0564    6  0.031414   1   2
186          1    187   -0.0047   -0.0000     100.0   518.67   643.32  1592.10  1427.27    14.62    21.61   551.08  2388.29  9037.71       1.3     48.23    519.53   2388.28   8115.67    8.5218      0.03       396      2388     100.0     38.42   23.0822    5  0.026178   1   2
187          1    188   -0.0067    0.0003     100.0   518.67   643.75  1602.38  1422.78    14.62    21.61   551.94  2388.31  9037.91       1.3     48.00    519.79   2388.23   8117.69    8.5207      0.03       396      2388     100.0     38.51   22.9588    4  0.020942   1   2
188          1    189   -0.0006    0.0002     100.0   518.67   644.18  1596.17  1428.01    14.62    21.61   550.70  2388.27  9044.55       1.3     48.08    519.58   2388.33   8117.51    8.5183      0.03       395      2388     100.0     38.48   23.1127    3  0.015707   1   2
189          1    190   -0.0027    0.0001     100.0   518.67   643.64  1599.22  1425.95    14.62    21.61   551.29  2388.29  9040.58       1.3     48.33    520.04   2388.35   8112.58    8.5223      0.03       398      2388     100.0     38.49   23.0675    2  0.010471   1   2
190          1    191   -0.0000   -0.0004     100.0   518.67   643.34  1602.36  1425.77    14.62    21.61   550.92  2388.28  9042.76       1.3     48.15    519.57   2388.30   8114.61    8.5174      0.03       394      2388     100.0     38.45   23.1295    1  0.005236   1   2
191          1    192    0.0009   -0.0000     100.0   518.67   643.54  1601.41  1427.20    14.62    21.61   551.25  2388.32  9033.22       1.3     48.25    520.08   2388.32   8110.93    8.5113      0.03       396      2388     100.0     38.48   22.9649    0  0.000000   1   2
192          2      1   -0.0018    0.0006     100.0   518.67   641.89  1583.84  1391.28    14.62    21.60   554.53  2388.01  9054.72       1.3     46.93    522.33   2388.06   8137.72    8.3905      0.03       391      2388     100.0     38.94   23.4585  286  1.000000   0   0
193          2      2    0.0043   -0.0003     100.0   518.67   641.82  1587.05  1393.13    14.62    21.61   554.77  2387.98  9051.31       1.3     47.24    522.70   2387.98   8131.09    8.4167      0.03       392      2388     100.0     39.06   23.4085  285  0.996503   0   0
194          2      3    0.0018    0.0003     100.0   518.67   641.55  1588.32  1398.96    14.62    21.60   555.14  2388.04  9054.24       1.3     47.22    522.58   2387.99   8140.58    8.3802      0.03       391      2388     100.0     39.11   23.4250  284  0.993007   0   0

In [167]:
val.iloc[25:35]

engine_id  cycle  setting1  setting2  setting3  sensor1  sensor2  sensor3  sensor4  sensor5  sensor6  sensor7  sensor8  sensor9  sensor10  sensor11  sensor12  sensor13  sensor14  sensor15  sensor16  sensor17  sensor18  sensor19  sensor20  sensor21  RUL  RUL_frac  w0  w1
25          1     26    0.0047   -0.0005     100.0   518.67   642.48  1583.28  1408.07    14.62    21.61   554.59  2388.08  9053.43       1.3     47.33    521.95   2388.07   8129.12    8.3949      0.03       391      2388     100.0     38.77   23.3557  117  0.823944   0   0
26          1     27   -0.0007    0.0001     100.0   518.67   642.08  1586.65  1400.31    14.62    21.61   554.35  2388.09  9046.10       1.3     47.34    521.82   2388.02   8127.24    8.4494      0.03       392      2388     100.0     38.87   23.3931  116  0.816901   0   0
27          1     28    0.0022    0.0005     100.0   518.67   641.93  1594.25  1401.29    14.62    21.61   553.56  2388.07  9055.56       1.3     47.05    521.84   2388.07   8134.89    8.4470      0.03       392      2388     100.0     38.83   23.3502  115  0.809859   0   0
28          1     29    0.0014    0.0001     100.0   518.67   641.95  1587.15  1398.11    14.62    21.61   554.15  2388.08  9046.11       1.3     47.42    522.39   2388.07   8133.13    8.4212      0.03       392      2388     100.0     39.02   23.3621  114  0.802817   0   0
29          1     30   -0.0025    0.0004     100.0   518.67   642.79  1585.72  1400.97    14.62    21.61   554.10  2388.09  9047.45       1.3     47.40    521.78   2388.10   8134.79    8.4110      0.03       391      2388     100.0     39.09   23.4069  113  0.795775   0   0
30          1     31   -0.0006    0.0004     100.0   518.67   642.58  1581.22  1398.91    14.62    21.61   554.42  2388.08  9056.40       1.3     47.23    521.79   2388.06   8130.11    8.4024      0.03       393      2388     100.0     38.81   23.3552  112  0.788732   0   0
31          5      1    0.0024   -0.0004     100.0   518.67   642.43  1590.79  1402.02    14.62    21.61   553.50  2388.07  9051.54       1.3     47.37    522.20   2388.07   8130.90    8.4426      0.03       394      2388     100.0     39.04   23.3916  188  1.000000   0   0
32          5      2    0.0011    0.0002     100.0   518.67   642.85  1581.46  1409.70    14.62    21.61   553.44  2388.06  9051.90       1.3     47.54    521.63   2388.11   8128.71    8.4429      0.03       393      2388     100.0     38.87   23.3181  187  0.994681   0   0
33          5      3    0.0056   -0.0000     100.0   518.67   642.88  1586.05  1407.64    14.62    21.61   553.51  2388.06  9057.29       1.3     47.27    521.80   2388.11   8132.02    8.4657      0.03       393      2388     100.0     39.02   23.3529  186  0.989362   0   0
34          5      4   -0.0010    0.0003     100.0   518.67   642.79  1585.93  1403.47    14.62    21.61   553.93  2388.15  9048.64       1.3     47.43    521.80   2388.09   8130.10    8.4147      0.03       392      2388     100.0     38.98   23.3574  185  0.984043   0   0

In [143]:
RUL_cols = ['engine_id', 'cycle', 'RUL', 'RUL_frac', 'w0', 'w1']
train.iloc[172:193][RUL_cols]

engine_id  cycle  RUL  RUL_frac  w0  w1
172          1    173   20  0.104167   1   1
173          1    174   19  0.098958   1   1
174          1    175   18  0.093750   1   1
175          1    176   17  0.088542   1   1
176          1    177   16  0.083333   1   1
177          1    178   15  0.078125   1   2
178          1    179   14  0.072917   1   2
179          1    180   13  0.067708   1   2
180          1    181   12  0.062500   1   2
181          1    182   11  0.057292   1   2
182          1    183   10  0.052083   1   2
183          1    184    9  0.046875   1   2
184          1    185    8  0.041667   1   2
185          1    186    7  0.036458   1   2
186          1    187    6  0.031250   1   2
187          1    188    5  0.026042   1   2
188          1    189    4  0.020833   1   2
189          1    190    3  0.015625   1   2
190          1    191    2  0.010417   1   2
191          1    192    1  0.005208   1   2
192          2      1  287  1.000000   0   0

In [31]:
def check_overwrite(filepath):
    if os.path.exists(filepath):
        overwrite = input('Pickle exists, overwrite? (y/n) ')
        overwrite = (overwrite.lower() == 'y')
    else:
        overwrite = True
    
    return overwrite


def checkpoint_items(checkpoint_name, items):
    filepath = os.path.join('pickle', str(checkpoint_name) + '.pkl')
    
    if check_overwrite(filepath):
        print('Saving items to', filepath)
        with open(filepath, 'wb') as f:
            pickle.dump(items, f)
            f.close()
        print('Items saved!')
    
    else:
        print('Did not save', checkpoint_name)
        

def load_checkpoint(checkpoint_name):
    filepath = os.path.join('pickle', str(checkpoint_name) + '.pkl')
    print('Loading', filepath)
    with open(filepath, 'rb') as f:
        items = pickle.load(f)
        f.close()
    print('Items loaded!')
    return items

In [16]:
pandas_profiling.ProfileReport(train)

In [17]:
pandas_profiling.ProfileReport(val)

In [10]:
checkpoint_items('initial_dfs', (train, val, test))

Pickle exists, overwrite? (y/n) y
Saving items to pickle/initial_dfs.pkl
Items saved!


In [32]:
train, val, test = load_checkpoint('initial_dfs')

Loading pickle/initial_dfs.pkl
Items loaded!


In [33]:
dfs = (train, val, test)

In [34]:
cols_to_drop = ['sensor1', 'sensor10', 'sensor16', 'sensor18', 'sensor19', 'sensor5', 'setting3', 'sensor6']
target_cols = ['RUL', 'RUL_frac', 'w0', 'w1']

In [35]:
def drop_col_list(dfs, cols_to_drop):
    for df in dfs:
        df.drop(cols_to_drop, inplace=True, axis=1)

In [36]:
drop_col_list(dfs, cols_to_drop)
check_df_shapes([train, val, test])

In [37]:
def geo_std(sequence):
    if 0 in sequence.unique():
        return 1
    else:
        geo_mean = gmean(sequence)
        summand = sum([np.log(value / geo_mean) ** 2 for value in sequence])
        return np.exp(np.sqrt(summand / len(sequence)))

In [38]:
stat_map = {'amean': np.mean,
            'gmean': gmean,
            'median': np.median,
            'std': np.std,
            'geo_std': geo_std}

In [41]:
def add_windowed_aggs(dfs, window_size, stat_map, verbose=True):
    for df in dfs:
        for col in df.columns:
            if col.startswith('sensor'):
                if verbose:
                    print(col)
                add_stats(df, col, window_size, stat_map)
    

def add_stats(df, col, window_size, stat_map):
    for stat in stat_map.keys():
        new_name = col + f'_{stat}'
        df[new_name] = (df.groupby('engine_id')[col]
                        .rolling(window_size)
                        .apply(lambda x: stat_map[stat](pd.Series(x)))
                        .reset_index()
                        [col]
                        .fillna(method='bfill'))

In [42]:
add_windowed_aggs(dfs, 5, stat_map)
check_df_shapes(dfs)

sensor2


/home/bam/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:15: FutureWarning: Currently, 'apply' passes the values as ndarrays to the applied function. In the future, this will change to passing it as Series objects. You need to specify 'raw=True' to keep the current behaviour, and you can pass 'raw=False' to silence this warning
  from ipykernel import kernelapp as app


sensor3
sensor4
sensor7
sensor8
sensor9
sensor11
sensor12
sensor13
sensor14
sensor15
sensor17
sensor20
sensor21
sensor2
sensor3
sensor4
sensor7
sensor8
sensor9
sensor11
sensor12
sensor13
sensor14
sensor15
sensor17
sensor20
sensor21
sensor2
sensor3
sensor4
sensor7
sensor8
sensor9
sensor11
sensor12
sensor13
sensor14
sensor15
sensor17
sensor20
sensor21


In [45]:
checkpoint_items('aggregate_dfs', dfs)

Pickle exists, overwrite? (y/n) y
Saving items to pickle/aggregate_dfs.pkl
Items saved!


In [15]:
train, val, test = load_checkpoint('aggregate_dfs')

Loading pickle/aggregate_dfs.pkl
Items loaded!


In [43]:
train.head(10)

engine_id  cycle  setting1  setting2  sensor2  sensor3  sensor4  sensor7  sensor8  sensor9  sensor11  sensor12  sensor13  sensor14  sensor15  sensor17  sensor20  sensor21  RUL  RUL_frac  w1  w0  sensor2_amean  sensor2_gmean  sensor2_median  sensor2_std  sensor2_geo_std  sensor3_amean  sensor3_gmean  sensor3_median  sensor3_std  sensor3_geo_std  sensor4_amean  sensor4_gmean  sensor4_median  sensor4_std  sensor4_geo_std  sensor7_amean  sensor7_gmean  sensor7_median  sensor7_std  sensor7_geo_std  sensor8_amean  sensor8_gmean  sensor8_median  sensor8_std  sensor8_geo_std  sensor9_amean  sensor9_gmean  sensor9_median  sensor9_std  sensor9_geo_std  sensor11_amean  sensor11_gmean  sensor11_median  sensor11_std  sensor11_geo_std  sensor12_amean  sensor12_gmean  sensor12_median  sensor12_std  sensor12_geo_std  sensor13_amean  sensor13_gmean  sensor13_median  sensor13_std  sensor13_geo_std  sensor14_amean  sensor14_gmean  sensor14_median  sensor14_std  sensor14_geo_std  sensor15_amean  \
0          1      1   -0.0007   -0.0004   641.82  1589.70  1400.60   554.36  2388.06  9046.19     47.47    521.66   2388.02   8138.62    8.4195       392     39.06   23.4190  191  1.000000   0   0        642.208     642.207966          642.35     0.209990         1.000327       1587.030    1587.025813         1587.99     3.645397         1.002300       1403.206    1403.204671         1403.14     1.931462         1.001377        554.164     554.163941          554.26     0.256016         1.000462       2388.070       2388.070         2388.06     0.023664         1.000010       9049.566    9049.565070         9049.48     4.103065         1.000453          47.328       47.327807            47.28      0.135115          1.002859         522.282      522.281857           522.28      0.386906          1.000741        2388.048        2388.048          2388.04      0.023152          1.000010        8134.194     8134.193654          8133.80      2.371418          1.000292         8.41334   
1          1      2    0.0019   -0.0003   642.15  1591.82  1403.14   553.75  2388.04  9044.07     47.49    522.28   2388.07   8131.49    8.4318       392     39.00   23.4236  190  0.994764   0   0        642.208     642.207966          642.35     0.209990         1.000327       1587.030    1587.025813         1587.99     3.645397         1.002300       1403.206    1403.204671         1403.14     1.931462         1.001377        554.164     554.163941          554.26     0.256016         1.000462       2388.070       2388.070         2388.06     0.023664         1.000010       9049.566    9049.565070         9049.48     4.103065         1.000453          47.328       47.327807            47.28      0.135115          1.002859         522.282      522.281857           522.28      0.386906          1.000741        2388.048        2388.048          2388.04      0.023152          1.000010        8134.194     8134.193654          8133.80      2.371418          1.000292         8.41334   
2          1      3   -0.0043    0.0003   642.35  1587.99  1404.20   554.26  2388.08  9052.94     47.27    522.42   2388.03   8133.23    8.4178       390     38.95   23.3442  189  0.989529   0   0        642.208     642.207966          642.35     0.209990         1.000327       1587.030    1587.025813         1587.99     3.645397         1.002300       1403.206    1403.204671         1403.14     1.931462         1.001377        554.164     554.163941          554.26     0.256016         1.000462       2388.070       2388.070         2388.06     0.023664         1.000010       9049.566    9049.565070         9049.48     4.103065         1.000453          47.328       47.327807            47.28      0.135115          1.002859         522.282      522.281857           522.28      0.386906          1.000741        2388.048        2388.048          2388.04      0.023152          1.000010        8134.194     8134.193654          8133.80      2.371418          1.000292         8.41334   
3          1      4

In [44]:
train.iloc[20]

engine_id              1.000000
cycle                 21.000000
setting1              -0.001200
setting2               0.000100
sensor2              642.370000
sensor3             1586.070000
sensor4             1398.130000
sensor7              554.080000
sensor8             2388.110000
sensor9             9048.150000
sensor11              47.150000
sensor12             522.420000
sensor13            2388.080000
sensor14            8134.020000
sensor15               8.404900
sensor17             392.000000
sensor20              39.090000
sensor21              23.310100
RUL                  171.000000
RUL_frac               0.895288
w1                     0.000000
w0                     0.000000
sensor2_amean        642.480000
sensor2_gmean        642.479871
sensor2_median       642.580000
sensor2_std            0.407774
sensor2_geo_std        1.000635
sensor3_amean       1586.148000
sensor3_gmean       1586.144676
sensor3_median      1586.070000
sensor3_std            3.247284
sensor3_

In [18]:
input_cols = ['engine', 'cycle']
linreg_tng_cols = list(set(train.columns).difference(set(target_cols)).difference(set(input_cols)))

In [19]:
linreg_noregular = LinearRegression()
linreg_noregular_X = train[linreg_tng_cols].copy()
linreg_noregular_y = train['RUL_frac'].copy()

linreg_noregular.fit(linreg_noregular_X, linreg_noregular_y)
linreg_noregular.score(linreg_noregular_X, linreg_noregular_y)

0.6781285259519296

In [20]:
linreg_noregular_val_X = val[linreg_tng_cols].copy()
linreg_noregular_val_y = val['RUL_frac'].copy()
linreg_noregular.score(linreg_noregular_val_X, linreg_noregular_val_y)

0.447466288759126

In [21]:
train.groupby('engine_id')['cycle'].max().reset_index()['cycle'].unique() > 125

array([ True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True,  True,  True,  True,  True,  True,  True,
        True,  True,  True])

In [22]:
val.groupby('engine_id')['cycle'].max().reset_index()['cycle'].unique() > 125

array([False, False, False,  True,  True, False,  True,  True, False,
       False,  True,  True,  True,  True, False,  True,  True,  True,
        True,  True,  True,  True,  True,  True, False,  True,  True,
        True, False, False, False,  True,  True,  True, False, False,
       False,  True,  True, False,  True, False,  True,  True, False,
        True])

In [23]:
lr_noreg = LinearRegression()

cutoff_train_125_cycles = train['cycle'] > 125

lr_noreg_X = train[cutoff_train_125_cycles][linreg_tng_cols].copy()
lr_noreg_y = train[cutoff_train_125_cycles]['RUL_frac'].copy()

lr_noreg.fit(lr_noreg_X, lr_noreg_y)
lr_noreg.score(lr_noreg_X, lr_noreg_y)

0.8139820027846307

In [24]:
cutoff_val_125_cycles = val['cycle'] > 125

lr_noreg_val_X = val[cutoff_val_125_cycles][linreg_tng_cols].copy()
lr_noreg_val_y = val[cutoff_val_125_cycles]['RUL_frac'].copy()
lr_noreg.score(lr_noreg_val_X, lr_noreg_val_y)

0.6340534166392304